In [1]:
import os,sys
import tensorflow as tf
# import importlib
sys.path.append('/home/ubuntu/hacking/projects/deep-mediation/nov2020')
import auxiliaryfunctions
# importlib.reload(auxiliaryfunctions)
import statsmodels.api as sm
import statsmodels.formula.api as smf
import seaborn as sns
import numpy as np
from scipy.stats import zscore,norm
from keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
import os
import pandas as pd
import random as python_random

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error,make_scorer,mean_absolute_error,r2_score

# from datagenerator import dataGenerator
from keras import backend as K

from tensorflow.keras.callbacks import LearningRateScheduler, ModelCheckpoint, EarlyStopping
from keras.optimizers import Adam, SGD


Bad key savefig.frameon in file /home/ubuntu/anaconda3/envs/deep_structure/lib/python3.6/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle, line 421 ('savefig.frameon : True')
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.3.3/matplotlibrc.template
or from the matplotlib source distribution

Bad key verbose.level in file /home/ubuntu/anaconda3/envs/deep_structure/lib/python3.6/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle, line 472 ('verbose.level  : silent      # one of silent, helpful, debug, debug-annoying')
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.3.3/matplotlibrc.template
or from the matplotlib source distribution

Bad key verbose.fileo in file /home/ubuntu/anaconda3/envs/deep_structure/lib/python3.6/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle, line 473 ('verbose.fileo  : sys.stdout  # a log filen

In [2]:
np.random.seed(123)
python_random.seed(123)
tf.random.set_seed(1234)

early_stopping = True
epochs = 1000
batch_size = 4
use_dynamic_LR=False
# optimizer='Adam'
algo = 'shallow' #['shallow','deep','svr'] 
patience = 50
result_path = '/home/ubuntu/hacking/projects/deep-mediation/nov2020/results/simulation-2-results'
num_subs = 1000
num_iters = 20
num_runs = 100
new_shape = [[32,32]] #[[8,8],[32,32],[64,64]]

In [3]:
def make_plot(z,m,d,iter):
    plt.figure(figsize=(20,5))
    plt.subplot(1, 4, 1)
    plot_distribution(z,m,labels=['z','m'])

    plt.subplot(1, 4, 2)
    plot_distribution(z,d,labels=['z','d'])

    plt.subplot(1, 4, 3)
    plot_scatter(z,d,labels= ['z','d'])

    plt.subplot(1, 4, 4)
    plot_scatter(z,m,labels= ['z','m'])
    # plt.savefig(os.path.join(result_path,'result'+ str(iter) +'.png'),dpi=300)
    plt.show()

def plot_distribution(z,m,labels):
    sns.distplot(z, hist=True, rug=True,label=labels[0]);
    sns.distplot(m, hist=True, rug=True,label=labels[1]);
    plt.legend()

def plot_scatter(y_test,y_pred,labels):
    r = np.corrcoef(y_pred,y_test)[0,1]
    r = round(r,3)
    plt.scatter(y_test,y_pred)
    plt.xlabel(labels[0])
    plt.ylabel(labels[1])
    plt.title('r=%s'%r)

def plot_loss(history):
    plt.plot(history.history['loss'])
    plt.plot(history.history['val_loss'])
    plt.title('model loss')
    plt.ylabel('MSE')
    plt.xlabel('epoch')
    plt.legend(['train', 'val'], loc='upper left')
    plt.show()

def plot_error(ax,values,title,y_lab,num_iterations):
    ax.plot(values)
    ax.set_xlim([0,num_iterations])
    ax.set_xlabel('#iterations')
    ax.set_ylabel(y_lab)
    ax.set_title(title)

def create_empty_df(num_runs,num_iters):
    # Creates an empty dataFrame
    a = np.empty((num_runs,num_iters))
    a[:] = np.nan
    dataFrame = None
    parameters = ['alpha0', 'beta0','alpha','beta','gamma']
    for params in parameters:
        iter = ['iter_'+str(i) for i in range(num_iters)]
        pdindex = pd.MultiIndex.from_product([[params], iter],
                                             names=['parameters', 'runs']) 
        frame = pd.DataFrame(a, columns = pdindex,index = range(0,num_runs))
        dataFrame = pd.concat([dataFrame,frame],axis=1)
    return dataFrame

def simulate_mediation(df,M,params_df,model,algo,num_subs,batch_size,epochs,n,n_runs,iterations):
    """
    """
    early_stopping=True
    # Initialize z with some phi
    print("Using intial random model parameters")
#     if algo == 'svr':
#         z = svr.predict(M.flatten())
    z = model.predict(M) 
    try:
        z = np.concatenate(z)
    except:
        pass
    # plot_scatter(z,df.m,labels=['z','m'])
    
    for i in range(0,iterations):
        print('Starting iteration... %s'%(i+1))
        #Check for sign change
        if np.corrcoef(z,df.Y)[0,1] < 0 :
            z = z*(-1)
        # Check for scaling
        z= zscore(z)
        print(z[0:5])
        lm = smf.ols(formula='z ~ X', data=df).fit()
        alpha0 = lm.params.loc['Intercept']
        alph = lm.params.loc['X'] 

        lm = smf.ols(formula='Y ~ z + X', data=df).fit()
        beta0 = lm.params.Intercept 
        bet = lm.params.z
        gam = lm.params.X 
        resid_std = np.std(lm.resid)
        e = df.Y - beta0 - (df.X*gam)
        h = alpha0 + df.X*alph
        d = (((bet*e)+h)/((bet**2)+1))
#         d = zscore(d)

        if algo== 'svr':
            model = auxiliaryfunctions.create_svr_model(M,d)
            z = model.predict(M)
        else:
            adam = Adam(lr=0.001, decay=0.03)
            model.compile(loss='mean_absolute_error',optimizer=adam)
            if early_stopping:
                es = EarlyStopping(monitor='val_loss', mode='min', verbose=1,patience=20)
                history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,callbacks=[es],
                                  shuffle=True,validation_split = 0.3)
            else:
                history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,
                              shuffle=True,validation_split = 0.3)
            z = model.predict(M)
       
        params_df.loc[n_runs]['alpha0','iter_'+str(i)]=alpha0
        params_df.loc[n_runs]['beta0','iter_'+str(i)]=beta0
        params_df.loc[n_runs]['beta','iter_'+str(i)]=bet
        params_df.loc[n_runs]['gamma','iter_'+str(i)]=gam
        params_df.loc[n_runs]['alpha','iter_'+str(i)]=alph

        try:
            z = np.concatenate(z)
        except:
            pass
       
    return params_df,z,model


In [4]:
os.environ["CUDA_VISIBLE_DEVICES"]="0"

for n in new_shape:
    start = 40
    output_df = create_empty_df(num_runs,num_iters)
    for runs in range(start,num_runs):
        K.clear_session()
        print("Running simulation for image shape %s starting with %s runs"%(n,runs+1))
    # simulate the dataset
        df,mediator,z = auxiliaryfunctions.simulate_dataset(num_subs,resize= True,
                                          new_shape=n,algo=algo,visualize=False,alpha=0.2)
        # create a model 
        if algo == 'svr':
            model = auxiliaryfunctions.create_svr_model(mediator,df.m)
        elif algo== 'shallow':
            input_shape = (n[0],n[1]*4,1)
            model = auxiliaryfunctions.create_shallow_model2D(input_shape=input_shape)
        else:
            input_shape = (n[0],n[1]*4,1)
            model = auxiliaryfunctions.create_deep_model2D(input_shape=input_shape)

        params_df,z_final,model_ = simulate_mediation(df,mediator,output_df,
                                      model,algo,n,batch_size,epochs,
                                      n,runs,num_iters)
        params_df.to_excel(os.path.join(result_path,'simulation-2-image-size-'+str(n[0])+'-'+algo+'-part-1.xlsx'))

Running simulation for image shape [32, 32] starting with 41 runs
Using intial random model parameters
Starting iteration... 1
[ 2.1906514  -0.7822166   1.0092071  -0.15238881 -0.9306636 ]
Epoch 1/1000
175/175 [==============================] - 1s 4ms/step - loss: 10.5392 - val_loss: 0.3890
Epoch 2/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.3954 - val_loss: 0.2854
Epoch 3/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.3177 - val_loss: 0.2401
Epoch 4/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2933 - val_loss: 0.2213
Epoch 5/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2807 - val_loss: 0.2049
Epoch 6/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2581 - val_loss: 0.2097
Epoch 7/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2703 - val_loss: 0.2081
Epoch 8/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2583 - val_loss: 0

175/175 [==============================] - 0s 3ms/step - loss: 0.2524 - val_loss: 0.2101
Epoch 39/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2454 - val_loss: 0.2107
Epoch 40/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2511 - val_loss: 0.2091
Epoch 41/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2523 - val_loss: 0.2083
Epoch 42/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2506 - val_loss: 0.2086
Epoch 43/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2437 - val_loss: 0.2095
Epoch 44/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2450 - val_loss: 0.2101
Epoch 45/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2462 - val_loss: 0.2091
Epoch 46/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2646 - val_loss: 0.2093
Epoch 47/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2482 - v

175/175 [==============================] - 1s 4ms/step - loss: 0.2379 - val_loss: 0.2064
Epoch 70/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2373 - val_loss: 0.2065
Epoch 71/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2499 - val_loss: 0.2064
Epoch 72/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2314 - val_loss: 0.2062
Epoch 73/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2396 - val_loss: 0.2066
Epoch 74/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2344 - val_loss: 0.2064
Epoch 75/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2445 - val_loss: 0.2063
Epoch 76/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2376 - val_loss: 0.2064
Epoch 77/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2349 - val_loss: 0.2060
Epoch 78/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2502 - v

Epoch 1/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.2295 - val_loss: 0.2290
Epoch 2/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2125 - val_loss: 0.2174
Epoch 3/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2160 - val_loss: 0.2169
Epoch 4/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2091 - val_loss: 0.2162
Epoch 5/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2147 - val_loss: 0.2180
Epoch 6/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2175 - val_loss: 0.2172
Epoch 7/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2347 - val_loss: 0.2174
Epoch 8/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2290 - val_loss: 0.2151
Epoch 9/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2366 - val_loss: 0.2135
Epoch 10/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.234

175/175 [==============================] - 1s 3ms/step - loss: 0.2322 - val_loss: 0.2120
Epoch 15/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2192 - val_loss: 0.2113
Epoch 16/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2046 - val_loss: 0.2111
Epoch 17/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2171 - val_loss: 0.2122
Epoch 18/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2226 - val_loss: 0.2108
Epoch 19/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2205 - val_loss: 0.2098
Epoch 20/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2181 - val_loss: 0.2107
Epoch 21/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2184 - val_loss: 0.2109
Epoch 22/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2303 - val_loss: 0.2111
Epoch 23/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2286 - v

...

175/175 [==============================] - 0s 3ms/step - loss: 0.2046 - val_loss: 0.2086
Epoch 74/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2038 - val_loss: 0.2083
Epoch 75/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2168 - val_loss: 0.2085
Epoch 76/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2110 - val_loss: 0.2087
Epoch 77/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.1991 - val_loss: 0.2087
Epoch 78/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2121 - val_loss: 0.2088
Epoch 79/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2045 - val_loss: 0.2084
Epoch 80/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2125 - val_loss: 0.2082
Epoch 81/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2083 - val_loss: 0.2084
Epoch 82/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.2079 - v

175/175 [==============================] - 1s 4ms/step - loss: 0.1881 - val_loss: 0.2075
Epoch 43/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1996 - val_loss: 0.2078
Epoch 44/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1987 - val_loss: 0.2079
Epoch 45/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.2096 - val_loss: 0.2077
Epoch 46/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.2005 - val_loss: 0.2072
Epoch 47/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.2078 - val_loss: 0.2075
Epoch 48/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.2020 - val_loss: 0.2075
Epoch 49/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2067 - val_loss: 0.2077
Epoch 50/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2017 - val_loss: 0.2070
Epoch 51/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1905 - v

175/175 [==============================] - 1s 4ms/step - loss: 0.1974 - val_loss: 0.2084
Epoch 37/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2002 - val_loss: 0.2082
Epoch 38/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2017 - val_loss: 0.2077
Epoch 39/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1956 - val_loss: 0.2075
Epoch 40/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1981 - val_loss: 0.2080
Epoch 41/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1923 - val_loss: 0.2079
Epoch 42/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1867 - val_loss: 0.2078
Epoch 43/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1973 - val_loss: 0.2083
Epoch 44/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1975 - val_loss: 0.2084
Epoch 45/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.2077 - v

175/175 [==============================] - 1s 6ms/step - loss: 0.1494 - val_loss: 0.2164
Epoch 7/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.1554 - val_loss: 0.2162
Epoch 8/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1687 - val_loss: 0.2150
Epoch 9/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.1703 - val_loss: 0.2138
Epoch 10/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.1692 - val_loss: 0.2156
Epoch 11/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1783 - val_loss: 0.2152
Epoch 12/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.1695 - val_loss: 0.2127
Epoch 13/1000
175/175 [==============================] - 1s 5ms/step - loss: 0.1652 - val_loss: 0.2133
Epoch 14/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1787 - val_loss: 0.2129
Epoch 15/1000
175/175 [==============================] - 1s 4ms/step - loss: 0.1760 - val_

175/175 [==============================] - 1s 3ms/step - loss: 0.1931 - val_loss: 0.2096
Epoch 64/1000
175/175 [==============================] - 1s 3ms/step - loss: 0.2008 - val_loss: 0.2094
Epoch 65/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.1956 - val_loss: 0.2094
Epoch 66/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2056 - val_loss: 0.2093
Epoch 67/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2027 - val_loss: 0.2093
Epoch 68/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2081 - val_loss: 0.2095
Epoch 69/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.1983 - val_loss: 0.2095
Epoch 70/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2103 - val_loss: 0.2099
Epoch 71/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2023 - val_loss: 0.2097
Epoch 72/1000
175/175 [==============================] - 0s 3ms/step - loss: 0.2126 - v

In [5]:
params_df

parameters    alpha0                                                    \
runs          iter_0    iter_1    iter_2    iter_3    iter_4    iter_5   
0                NaN       NaN       NaN       NaN       NaN       NaN   
1                NaN       NaN       NaN       NaN       NaN       NaN   
2                NaN       NaN       NaN       NaN       NaN       NaN   
3                NaN       NaN       NaN       NaN       NaN       NaN   
4                NaN       NaN       NaN       NaN       NaN       NaN   
..               ...       ...       ...       ...       ...       ...   
95         -0.001963 -0.011314 -0.012735 -0.012962 -0.013045 -0.013113   
96         -0.000060  0.003312  0.003808  0.003853  0.003879  0.003916   
97         -0.002937 -0.007345 -0.008058 -0.008200 -0.008173 -0.008194   
98         -0.001585 -0.003290 -0.003631 -0.003608 -0.003638 -0.003651   
99          0.000011  0.000595  0.000678  0.000686  0.000694  0.000702   

parameters                                          ...     gamma            \
runs          iter_6    iter_7    iter_8    iter_9  ...   iter_10   iter_11   
0                NaN       NaN       NaN       NaN  ...       NaN       NaN   
1                NaN       NaN       NaN       NaN  ...       NaN       NaN   
2                NaN       NaN       NaN       NaN  ...       NaN       NaN   
3                NaN       NaN       NaN       NaN  ...       NaN       NaN   
4                NaN       NaN       NaN       NaN  ...       NaN       NaN   
..               ...       ...       ...       ...  ...       ...       ...   
95         -0.013192 -0.013122 -0.013163 -0.013117  ...  5.004001  5.000591   
96          0.003951  0.003935  0.003959  0.003964  ...  4.971605  4.973419   
97         -0.008148 -0.008179 -0.008135 -0.008145  ...  4.968590  4.967250   
98         -0.003671 -0.003688 -0.003695 -0.003708  ...  5.035207  5.039795   
99          0.000702  0.000703  0.000703  0.000701  ...  4.964531  4.968339   

parameters                                                              \
runs         iter_12   iter_13   iter_14   iter_15   iter_16   iter_17   
0                NaN       NaN       NaN       NaN       NaN       NaN   
1                NaN       NaN       NaN       NaN       NaN       NaN   
2                NaN       NaN       NaN       NaN       NaN       NaN   
3                NaN       NaN       NaN       NaN       NaN       NaN   
4                NaN       NaN       NaN       NaN       NaN       NaN   
..               ...       ...       ...       ...       ...       ...   
95          5.003310  5.000759  5.008796  5.005237  5.006042  5.006815   
96          4.967763  4.967921  4.964550  4.968560  4.964327  4.962803   
97          4.970244  4.964853  4.967192  4.962189  4.959590  4.958276   
98          5.032867  5.034301  5.035458  5.031967  5.026347  5.031849   
99          4.959628  4.969222  4.961088  4.962968  4.963083  4.964060   

parameters                      
runs         iter_18   iter_19  
0                NaN       NaN  
1                NaN       NaN  
2                NaN       NaN  
3                NaN       NaN  
4                NaN       NaN  
..               ...       ...  
95          5.001678  5.004200  
96          4.974441  4.972154  
97          4.961317  4.960896  
98          5.033652  5.035932  
99          4.963436  4.961546  

[100 rows x 100 columns]

In [6]:
result_path

'/home/ubuntu/hacking/projects/deep-mediation/nov2020/results/simulation-2-results'

In [8]:
!nvidia-smi

Sun Dec 13 16:42:37 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.51.06    Driver Version: 450.51.06    CUDA Version: 11.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   43C    P0    46W / 300W |  15653MiB / 16160MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-SXM2...  Off  | 00000000:00:05.0 Off |                    0 |
| N/A   

In [ ]:
!kill -9 11670

In [ ]:
ls ../results/simulation-2-results/

In [ ]:
params_df